In [66]:
#Imports
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from torchvision import datasets, transforms
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
import math
import os
import requests
import zipfile
from pathlib import Path
import random
import glob
from PIL import Image
import time

In [67]:
# Setup path to data folder
image_path = Path("data/")
def walk_through_dir(dir_path):
    for dirpath, dirnames, filenames in os.walk(image_path):
        print(f"There are {len(dirnames)} directories and {len(filenames)} images in '{dirpath}'.")
        

In [68]:
#Check if files are present in selected directory
walk_through_dir(image_path)

There are 2 directories and 3 images in 'data'.
There are 0 directories and 1 images in 'data/test'.
There are 0 directories and 357 images in 'data/train'.


In [69]:
# Setup train and testing paths
train_dir = image_path / "train"
test_dir = image_path / "test"

train_dir, test_dir

(PosixPath('data/train'), PosixPath('data/test'))

In [70]:
#  View Random image from the data files
# Set seed
random.seed(33) # <- try changing this and see what happens

# 1. Get all image paths (* means "any combination")
image_path_list = list(image_path.glob("*/*.jpg"))

# 2. Get random image path
random_image_path = random.choice(image_path_list)

# 3. Get image class from path name (the image class is the name of the directory where the image is stored)
image_class = random_image_path.parent.stem

# 4. Open image
img1 = Image.open(random_image_path)

# 5. Print metadata
print(f"Random image path: {random_image_path}")
print(f"Image class: {image_class}")
print(f"Image height: {img1.height}") 
print(f"Image width: {img1.width}")
img1

Random image path: data/train/ID2099464826.jpg
Image class: train
Image height: 1000
Image width: 2000


In [71]:


IMAGENET_MEAN = [0.485, 0.456, 0.406]
IMAGENET_STD = [0.229, 0.224, 0.225]

data_transform = transforms.Compose([
    # Resize the images to 512*512...............NB I chose this randomly 
    transforms.Resize(size=(512,512)),
    # Flip the images randomly on the horizontal
    transforms.RandomHorizontalFlip(p=0.5), # p = probability of flip, 0.5 = 50% chance Data augmentation to increase data variability
    # Turn the image into a torch.Tensor
    transforms.ToTensor(),# this also converts all pixel values from 0 to 255 to be between 0.0 and 1.0 
    transforms.Normalize(mean=IMAGENET_MEAN, std=IMAGENET_STD)
    
    
])

In [72]:
#Confirm that the transform works
data_transform(img1)


tensor([[[ 1.1700,  0.9474,  1.1358,  ...,  0.4166,  0.8789,  0.6049],
         [ 1.2728,  0.7419,  0.8789,  ...,  0.4679,  0.7933,  0.7762],
         [ 1.3755,  0.9132,  0.7248,  ...,  0.1426,  0.6563,  0.6392],
         ...,
         [ 0.5707,  0.8961,  0.4851,  ...,  0.4851,  1.7352,  2.1975],
         [ 0.1426,  0.3481,  0.4679,  ...,  0.7591,  1.4783,  2.1119],
         [-0.1999,  0.1083,  0.4851,  ...,  0.7591,  1.0159,  1.4783]],

        [[ 1.4307,  1.2381,  1.4482,  ...,  0.6954,  1.1856,  0.9055],
         [ 1.5707,  1.0630,  1.2556,  ...,  0.7129,  1.0980,  1.0980],
         [ 1.7108,  1.2556,  1.1331,  ...,  0.3627,  0.9405,  1.0105],
         ...,
         [ 0.8179,  1.1506,  0.6779,  ...,  0.6779,  1.9209,  2.4111],
         [ 0.5028,  0.6604,  0.7129,  ...,  0.9405,  1.6933,  2.3235],
         [ 0.2402,  0.4503,  0.7654,  ...,  0.9405,  1.2206,  1.6933]],

        [[ 1.5071,  1.2282,  1.2980,  ...,  0.5485,  1.1062,  1.0017],
         [ 1.5420,  0.9668,  0.9668,  ...,  0

In [73]:
data_transform(img1).shape

torch.Size([3, 512, 512])

In [74]:
class CustomImageDataset(Dataset):
    """
    Loads images from a single directory without requiring class subdirectories.
    """
    def __init__(self, root_dir, transform=None):
        self.root_dir = root_dir
        self.transform = transform
        
        self.image_paths = []
        # Collect paths for common image extensions
        for extension in ['jpg', 'jpeg', 'png', 'tiff']:
            pattern = os.path.join(self.root_dir, f'*.{extension}')
            self.image_paths.extend(glob.glob(pattern))
        
        if not self.image_paths:
            raise FileNotFoundError(f"No images found in the directory: {root_dir}")

    def __len__(self):
        return len(self.image_paths)

    def __getitem__(self, idx):
        img_path = self.image_paths[idx]
        image = Image.open(img_path).convert('RGB')
        
        if self.transform:
            image = self.transform(image)
        
        # Returns only the image tensor
        return image

In [75]:
train_dir = image_path / "train"
test_dir = image_path / "test"

# Assuming data_transform is defined (e.g., Resize, ToTensor)

# Create the custom datasets
try:
    train_data = CustomImageDataset(root_dir=train_dir, 
                                    transform=data_transform)

    test_data = CustomImageDataset(root_dir=test_dir, 
                                   transform=data_transform)
    print(f"Train data loaded: {len(train_data)} images")
    print(f"Test data loaded: {len(test_data)} images")

except FileNotFoundError as e:
    print(f"Error: {e}")
    print("Please ensure the 'train_dir' and 'test_dir' variables point to folders containing images.")

Train data loaded: 357 images
Test data loaded: 1 images


In [76]:
img_2 = train_data[0]
print(f"Image tensor:\n{img_2}")
print(f"Image shape: {img_2.shape}")
print(f"Image datatype: {img_2.dtype}")


Image tensor:
tensor([[[ 1.2214,  0.7933, -0.1999,  ...,  2.0777,  2.2318,  2.2318],
         [ 1.1015,  0.5364, -0.3712,  ...,  1.5810,  2.0434,  2.2147],
         [ 0.8447,  0.1083, -0.7479,  ...,  1.2385,  1.6153,  2.0948],
         ...,
         [-0.3027, -0.4911, -0.9020,  ..., -0.9192,  0.0056,  0.8104],
         [-0.0972, -0.7822, -0.9705,  ..., -0.6281,  0.2624,  1.2385],
         [-0.6965, -0.7822, -0.7822,  ..., -0.6109,  0.9988,  1.2385]],

        [[ 1.5707,  1.1506,  0.2052,  ...,  2.3060,  2.4286,  2.4286],
         [ 1.4482,  0.9230,  0.0301,  ...,  1.8333,  2.2535,  2.4111],
         [ 1.1856,  0.5203, -0.3025,  ...,  1.5532,  1.8683,  2.3060],
         ...,
         [ 0.3452,  0.0651, -0.3901,  ..., -0.3550,  0.4678,  1.2381],
         [ 0.5903, -0.1800, -0.4076,  ..., -0.1099,  0.6954,  1.6408],
         [ 0.0126, -0.1625, -0.1625,  ..., -0.1099,  1.4307,  1.6232]],

        [[ 1.5071,  0.7925, -0.3055,  ...,  2.4657,  2.6226,  2.6226],
         [ 1.3502,  0.5485, -0.

In [77]:
train_data_csv = pd.read_csv("data/train.csv")

In [78]:
train_data_csv.head()

sample_id              image_path Sampling_Date State  \
0  ID1011485656__Dry_Clover_g  train/ID1011485656.jpg      2015/9/4   Tas   
1    ID1011485656__Dry_Dead_g  train/ID1011485656.jpg      2015/9/4   Tas   
2   ID1011485656__Dry_Green_g  train/ID1011485656.jpg      2015/9/4   Tas   
3   ID1011485656__Dry_Total_g  train/ID1011485656.jpg      2015/9/4   Tas   
4         ID1011485656__GDM_g  train/ID1011485656.jpg      2015/9/4   Tas   

           Species  Pre_GSHH_NDVI  Height_Ave_cm   target_name   target  
0  Ryegrass_Clover           0.62         4.6667  Dry_Clover_g   0.0000  
1  Ryegrass_Clover           0.62         4.6667    Dry_Dead_g  31.9984  
2  Ryegrass_Clover           0.62         4.6667   Dry_Green_g  16.2751  
3  Ryegrass_Clover           0.62         4.6667   Dry_Total_g  48.2735  
4  Ryegrass_Clover           0.62         4.6667         GDM_g  16.2750

In [79]:
#To make sure the csv file matches the images file
for i, _ in train_data_csv.iterrows():
    train_data_csv.loc[i, "sample_id"] = train_data_csv.loc[i, "sample_id"].split("_")[0]
cols = [c for c in train_data_csv.columns if c not in ["target_name", "target"]]
df_static = (
    train_data_csv[cols]
      .drop_duplicates(subset="sample_id")
)

df_pivot = (
    train_data_csv.pivot(index="sample_id", columns="target_name", values="target")
      .rename(columns=lambda x: f"{x}_target")
      .reset_index()
)

df_final_train = df_static.merge(df_pivot, on="sample_id", how="left")

In [80]:
df_final_train.head()

sample_id              image_path Sampling_Date State  \
0  ID1011485656  train/ID1011485656.jpg      2015/9/4   Tas   
1  ID1012260530  train/ID1012260530.jpg      2015/4/1   NSW   
2  ID1025234388  train/ID1025234388.jpg      2015/9/1    WA   
3  ID1028611175  train/ID1028611175.jpg     2015/5/18   Tas   
4  ID1035947949  train/ID1035947949.jpg     2015/9/11   Tas   

             Species  Pre_GSHH_NDVI  Height_Ave_cm  Dry_Clover_g_target  \
0    Ryegrass_Clover           0.62         4.6667               0.0000   
1            Lucerne           0.55        16.0000               0.0000   
2  SubcloverDalkeith           0.38         1.0000               6.0500   
3           Ryegrass           0.66         5.0000               0.0000   
4           Ryegrass           0.54         3.5000               0.4343   

   Dry_Dead_g_target  Dry_Green_g_target  Dry_Total_g_target  GDM_g_target  
0            31.9984             16.2751             48.2735       16.2750  
1             0.0000              7.6000              7.6000        7.6000  
2             0.0000              0.0000              6.0500        6.0500  
3            30.9703             24.2376             55.2079       24.2376  
4            23.2239             10.5261             34.1844       10.9605

In [81]:
TARGET_COLUMNS = ['Dry_Dead_g_target', 'Dry_Green_g_target', 'Dry_Clover_g_target', 'GDM_g_target', 'Dry_Total_g_target']
N_OUTPUTS = len(TARGET_COLUMNS)
# Hyperparameters
BATCH_SIZE = 32         
LEARNING_RATE = 0.001
IMAGE_SIZE = 224        # Recommended native size for ResNet is 224x224
TEST_SIZE = 0.2
RANDOM_STATE = 42
FILE_ID_COLUMN = 'sample_id' 

# ImageNet Scaling Constants (MANDATORY for ResNet)
IMAGENET_MEAN = [0.485, 0.456, 0.406]
IMAGENET_STD = [0.229, 0.224, 0.225]

In [82]:
train_transforms = transforms.Compose([
    transforms.Resize((IMAGE_SIZE, IMAGE_SIZE)),
    transforms.RandomHorizontalFlip(p=0.5), 
    transforms.RandomRotation(degrees=10),   
                      # Converts PIL image to Tensor
    transforms.Normalize(mean=IMAGENET_MEAN, std=IMAGENET_STD)
])

# Testing Transforms (only includes resize and normalization)
test_transforms = transforms.Compose([
    transforms.Resize((IMAGE_SIZE, IMAGE_SIZE)),
                    # Converts PIL image to Tensor
    transforms.Normalize(mean=IMAGENET_MEAN, std=IMAGENET_STD)
])

In [91]:
class MultiTargetBiomassDataset(Dataset):
    """
    Dataset to load targets and images, applying Z-score scaling to targets.
    """
    def __init__(self, data_frame, tensor_data_dict, target_cols, tensor_filename_col, target_means, target_stds, transform=None):
        self.biomass_frame = data_frame
        self.tensor_dict = tensor_data_dict 
        self.target_cols = target_cols
        self.tensor_filename_col = tensor_filename_col
        self.target_means = target_means # Pytorch tensor of means
        self.target_stds = target_stds   # Pytorch tensor of STDs
        self.transform = transform       # Pass image transform here

    def __len__(self):
        return len(self.biomass_frame)

    def __getitem__(self, idx):
        # ... (Key Generation Logic remains the same) ...
        sample_id = self.biomass_frame.iloc[idx][self.tensor_filename_col]
        sample_id_str = str(sample_id)
        numeric_id_str = sample_id_str.lstrip('abcdefghijklmnopqrstuvwxyzABCDEFGHIJKLMNOPQRSTUVWXYZ')
        
        try:
            key = int(numeric_id_str) 
        except ValueError:
            key = sample_id_str

        if key not in self.tensor_dict:
             raise KeyError(f"Lookup key '{key}' not found in the tensor dictionary.")

        # 1. Load Image Tensor (already pre-processed to size)
        image_tensor = self.tensor_dict[key]
        
        # 2. Apply final transforms (ImageNet Normalization)
        if self.transform:
            image_tensor = self.transform(image_tensor) # This expects a PIL image, but since the tensor is loaded in memory, you need to adjust this IF your pre_loaded_tensors are TENSORS.
            

        # 3. Target Values Lookup & SCALING
        biomass_values = self.biomass_frame.iloc[idx][self.target_cols].astype(float).values
        target_tensor = torch.tensor(biomass_values, dtype=torch.float32)
        
        # --- APPLY Z-SCORE SCALING ---
        target_tensor = (target_tensor - self.target_means) / self.target_stds
        
        return image_tensor, target_tensor

In [84]:
def calculate_rmse(predictions, targets):
    """Calculates the Root Mean Squared Error (RMSE) over all outputs."""
    return torch.sqrt(F.mse_loss(predictions, targets, reduction='mean'))

def evaluate_model(model, data_loader, criterion, target_names, target_stds, target_means):
    """
    Evaluates the model, applying inverse scaling for interpretable RMSE.
    """
    model.eval() 
    all_preds = []
    all_targets = []
    
    with torch.no_grad(): 
        for images, targets in data_loader:
            predictions = model(images)
            all_preds.append(predictions)
            all_targets.append(targets)

    preds_scaled = torch.cat(all_preds)
    targets_scaled = torch.cat(all_targets)

    # --- INVERSE SCALING ---
    preds_tensor = (preds_scaled * target_stds) + target_means
    targets_tensor = (targets_scaled * target_stds) + target_means
    
    # Calculate performance metrics on the original (unscaled) values
    test_loss = criterion(preds_tensor, targets_tensor).item() # Loss on unscaled values
    total_rmse = calculate_rmse(preds_tensor, targets_tensor).item()
    
    individual_rmse = {}
    for i, name in enumerate(target_names):
        target_col = targets_tensor[:, i]
        pred_col = preds_tensor[:, i]
        rmse_col = torch.sqrt(F.mse_loss(pred_col, target_col)).item()
        individual_rmse[name] = rmse_col
    
    return test_loss, total_rmse, individual_rmse

In [85]:

class MultiOutputBiomassPredictorCNN(nn.Module):
    def __init__(self, num_outputs, image_size= IMAGE_SIZE):
        super(MultiOutputBiomassPredictorCNN, self).__init__()
        
        self.features = nn.Sequential(
            nn.Conv2d(3, 16, kernel_size=3, padding=1),
            nn.ReLU(), 
            nn.MaxPool2d(kernel_size=2, stride=2),
            nn.Conv2d(16, 32, kernel_size=3, padding=1),
            nn.ReLU(), 
            nn.MaxPool2d(kernel_size=2, stride=2) 
        )
        
        flattened_size = 32 * (image_size // 4) * (image_size // 4)

        self.regressor = nn.Sequential(
            nn.Linear(flattened_size, 128), nn.ReLU(), nn.Dropout(0.5),
            nn.Linear(128, num_outputs) 
        )

    def forward(self, x):
        x = self.features(x)
        x = x.view(x.size(0), -1)
        x = self.regressor(x)
        return x

In [86]:
df_full = df_final_train
pre_loaded_tensors = {
    int(row[FILE_ID_COLUMN].lstrip('abcdefghijklmnopqrstuvwxyzABCDEFGHIJKLMNOPQRSTUVWXYZ')): torch.rand(3, IMAGE_SIZE, IMAGE_SIZE) 
    for index, row in df_full.iterrows()}

In [87]:
df_train, df_test = train_test_split(
    df_full, 
    test_size=TEST_SIZE, 
    random_state=RANDOM_STATE
)
df_train = df_train.reset_index(drop=True)
df_test = df_test.reset_index(drop=True)

In [88]:
target_means_np = df_train[TARGET_COLUMNS].mean().values
target_stds_np = df_train[TARGET_COLUMNS].std().values

TARGET_MEANS_TENSOR = torch.tensor(target_means_np, dtype=torch.float32)
TARGET_STDS_TENSOR = torch.tensor(target_stds_np, dtype=torch.float32)

print(f"Target Means (g) for Scaling: {target_means_np}")
print(f"Target STDs (g) for Scaling: {target_stds_np}")
print("-" * 50)

Target Means (g) for Scaling: [12.00621404 27.48919474  6.25504667 33.74424105 45.74937158]
Target STDs (g) for Scaling: [12.49503653 26.18853209 11.75210405 25.62058452 28.86353229]
--------------------------------------------------


In [89]:
train_dataset = MultiTargetBiomassDataset(
    data_frame=df_train, 
    tensor_data_dict=pre_loaded_tensors, 
    target_cols=TARGET_COLUMNS, 
    tensor_filename_col=FILE_ID_COLUMN,
    target_means=TARGET_MEANS_TENSOR, 
    target_stds=TARGET_STDS_TENSOR,
    transform=train_transforms
)
test_dataset = MultiTargetBiomassDataset(
    data_frame=df_test, 
    tensor_data_dict=pre_loaded_tensors, 
    target_cols=TARGET_COLUMNS, 
    tensor_filename_col=FILE_ID_COLUMN,
    target_means=TARGET_MEANS_TENSOR, 
    target_stds=TARGET_STDS_TENSOR,
    transform=test_transforms
)

train_loader = DataLoader(train_dataset, batch_size=BATCH_SIZE, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=BATCH_SIZE, shuffle=False)

In [90]:
start_time = time.time() 

model = MultiOutputBiomassPredictorCNN(num_outputs=N_OUTPUTS, image_size=IMAGE_SIZE) 
criterion = nn.MSELoss() 
optimizer = optim.Adam(model.parameters(), lr=LEARNING_RATE)

# Adding Learning Rate Scheduler (Recommended Optimization)
scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=7, gamma=0.1)

print(f"\n--- Starting Training (CNN) ---")

for epoch in range(20): # Increased epochs to 20 for better convergence
    # --- TRAINING PHASE ---
    model.train()
    running_loss = 0.0
    
    for images, targets in train_loader:
        # Check for None items due to mock data handling (remove for real data)
        if images is None or targets is None: continue 
        
        optimizer.zero_grad()
        predictions = model(images)
        loss = criterion(predictions, targets) # Loss calculated on SCALED values
        loss.backward()
        optimizer.step()
        running_loss += loss.item()
    
    train_avg_loss_scaled = running_loss / len(train_loader)

    # --- VALIDATION/TESTING PHASE ---
    # Passing scaling tensors for inverse calculation
    test_avg_loss_unscaled, total_rmse, individual_rmse = evaluate_model(
        model, test_loader, criterion, TARGET_COLUMNS, TARGET_STDS_TENSOR, TARGET_MEANS_TENSOR
    )
    
    # Step the scheduler
    scheduler.step()
    
    print(f"\n>>> EPOCH {epoch+1}/20 <<<")
    print(f"Train Loss (SCALED MSE): {train_avg_loss_scaled:.4f}")
    print(f"Test Loss (UNSCALED MSE): {test_avg_loss_unscaled:.4f} | Total Test RMSE: {total_rmse:.2f} g")

    print("Individual Target RMSE (grams, UNscaled):")
    for name, rmse in individual_rmse.items():
        print(f"  - {name}: {rmse:.2f} g")

print(f'\nDuration: {time.time() - start_time:.0f} seconds') 
print("\nTraining Complete.")


--- Starting Training (CNN) ---

>>> EPOCH 1/20 <<<
Train Loss (SCALED MSE): 66.9475
Test Loss (UNSCALED MSE): 528.0261 | Total Test RMSE: 22.98 g
Individual Target RMSE (grams, UNscaled):
  - Dry_Dead_g_target: 13.49 g
  - Dry_Green_g_target: 23.15 g
  - Dry_Clover_g_target: 20.50 g
  - GDM_g_target: 25.41 g
  - Dry_Total_g_target: 29.26 g

>>> EPOCH 2/20 <<<
Train Loss (SCALED MSE): 1.6601
Test Loss (UNSCALED MSE): 402.9427 | Total Test RMSE: 20.07 g
Individual Target RMSE (grams, UNscaled):
  - Dry_Dead_g_target: 12.05 g
  - Dry_Green_g_target: 24.64 g
  - Dry_Clover_g_target: 13.66 g
  - GDM_g_target: 22.15 g
  - Dry_Total_g_target: 24.18 g

>>> EPOCH 3/20 <<<
Train Loss (SCALED MSE): 1.0065
Test Loss (UNSCALED MSE): 384.5473 | Total Test RMSE: 19.61 g
Individual Target RMSE (grams, UNscaled):
  - Dry_Dead_g_target: 12.08 g
  - Dry_Green_g_target: 22.68 g
  - Dry_Clover_g_target: 13.43 g
  - GDM_g_target: 22.24 g
  - Dry_Total_g_target: 24.24 g

>>> EPOCH 4/20 <<<
Train Loss (SCAL

In [92]:
def create_comparison_table(predicted_targets_np, actual_targets_np, sample_id_str, target_cols):
    
    # Calculate absolute error for each target
    error_np = np.abs(predicted_targets_np - actual_targets_np)
    
    comparison_data = {
        'Target': target_cols,
        'Actual (g)': actual_targets_np,
        'Predicted (g)': predicted_targets_np,
        'Error (g)': error_np
    }
    
    comparison_df = pd.DataFrame(comparison_data)

    # Format numeric columns for clean display (2 decimal places)
    comparison_df['Actual (g)'] = comparison_df['Actual (g)'].map('{:.2f}'.format)
    comparison_df['Predicted (g)'] = comparison_df['Predicted (g)'].map('{:.2f}'.format)
    comparison_df['Error (g)'] = comparison_df['Error (g)'].map('{:.2f}'.format)

    print(f"\n--- Model Prediction vs. Actual for Sample ID: {sample_id_str} ---")
    print(comparison_df.to_string(index=False))

    # Calculate Total RMSE (Root Mean Square Error) for this single sample
    single_sample_rmse = np.sqrt(np.mean((predicted_targets_np - actual_targets_np)**2))
    print(f"\nSingle Sample Total RMSE: {single_sample_rmse:.2f} g")
    
    return comparison_df


# 1. Actual Targets (Ground Truth)
actual_targets_np_mock = np.array([45.0, 30.5, 8.1, 84.0, 105.0]) 

# 2. Predicted Targets (Your model's output after inverse scaling)
# Simulate a reasonable prediction close to the actual values
predicted_targets_np_mock = actual_targets_np_mock + np.array([1.5, -2.1, 0.5, -1.0, 0.9])

sample_id_mock = "ID142" 

# Run the comparison
create_comparison_table(
    predicted_targets_np=predicted_targets_np_mock,
    actual_targets_np=actual_targets_np_mock,
    sample_id_str=sample_id_mock,
    target_cols=TARGET_COLUMNS
)


--- Model Prediction vs. Actual for Sample ID: ID142 ---
             Target Actual (g) Predicted (g) Error (g)
  Dry_Dead_g_target      45.00         46.50      1.50
 Dry_Green_g_target      30.50         28.40      2.10
Dry_Clover_g_target       8.10          8.60      0.50
       GDM_g_target      84.00         83.00      1.00
 Dry_Total_g_target     105.00        105.90      0.90

Single Sample Total RMSE: 1.32 g


Target Actual (g) Predicted (g) Error (g)
0    Dry_Dead_g_target      45.00         46.50      1.50
1   Dry_Green_g_target      30.50         28.40      2.10
2  Dry_Clover_g_target       8.10          8.60      0.50
3         GDM_g_target      84.00         83.00      1.00
4   Dry_Total_g_target     105.00        105.90      0.90

In [62]:
def run_random_prediction_comparison(model, df_test, image_tensor_dict, scaler, transforms, target_cols, file_id_col):
    """
    Picks a random sample from the test set, performs inference, inverse-scales,
    and displays the comparison table.
    """
    model.eval()
    
    # 1. Select a random sample
    sample_index = random.randint(0, len(df_test) - 1)
    sample_row = df_test.iloc[sample_index]
    
    # 2. Get sample data and key
    sample_id = sample_row[file_id_col]
    sample_id_str = str(sample_id)
    
    numeric_id_str = sample_id_str.lstrip('abcdefghijklmnopqrstuvwxyzABCDEFGHIJKLMNOPQRSTUVWXYZ')
    try:
        key = int(numeric_id_str) 
    except ValueError:
        key = sample_id_str
    
    if key not in image_tensor_dict:
        print(f"Error: Image key '{key}' not found in dictionary.")
        return

    # 3. Prepare Image Input (Input Scaling)
    image_tensor = image_tensor_dict[key]
    input_tensor = transforms(image_tensor)
    input_tensor = input_tensor.unsqueeze(0) # Add batch dimension

    # 4. Make Prediction (on scaled inputs)
    with torch.no_grad():
        prediction_scaled_tensor = model(input_tensor) 

    # 5. Inverse Scaling (Output Scaling)
    predicted_scaled_np = prediction_scaled_tensor.cpu().numpy()
    predicted_targets_np = scaler.inverse_transform(predicted_scaled_np).flatten()

    # 6. Get Actual Targets (Ground Truth)
    actual_targets_np = sample_row[target_cols].astype(float).values
    
    # 7. Display Comparison Table
    comparison_df = create_comparison_table(
        predicted_targets_np=predicted_targets_np,
        actual_targets_np=actual_targets_np,
        sample_id_str=sample_id_str,
        target_cols=target_cols
    )
    
    # Export the comparison table to a CSV file (for your review)
    comparison_df.to_csv('single_sample_comparison.csv', index=False)
    print("\nResults saved to single_sample_comparison.csv")
    
    return comparison_df

In [65]:
from sklearn.preprocessing import StandardScaler
scaler = StandardScaler()
scaler.fit(df_train[TARGET_COLUMNS].values)
run_random_prediction_comparison(
    model=model,
    df_test=df_test,
    image_tensor_dict=pre_loaded_tensors,
    scaler=scaler,
    transforms=test_transforms,
    target_cols=TARGET_COLUMNS,
    file_id_col=FILE_ID_COLUMN
)


--- Model Prediction vs. Actual for Sample ID: ID290369222 ---
             Target Actual (g) Predicted (g) Error (g)
  Dry_Dead_g_target      11.47         12.21      0.73
 Dry_Green_g_target      40.85         25.45     15.39
Dry_Clover_g_target       0.00          7.23      7.23
       GDM_g_target      40.85         34.45      6.39
 Dry_Total_g_target      52.32         46.86      5.46

Single Sample Total RMSE: 8.49 g

Results saved to single_sample_comparison.csv


Target Actual (g) Predicted (g) Error (g)
0    Dry_Dead_g_target      11.47         12.21      0.73
1   Dry_Green_g_target      40.85         25.45     15.39
2  Dry_Clover_g_target       0.00          7.23      7.23
3         GDM_g_target      40.85         34.45      6.39
4   Dry_Total_g_target      52.32         46.86      5.46